In [1]:
import os
import h5py
import mediapy as media
import matplotlib.pyplot as plt

def load_hdf5(dataset_path):
    if not os.path.isfile(dataset_path):
        print(f'Dataset does not exist at \n{dataset_path}\n')
        exit()

    with h5py.File(dataset_path, 'r') as root:
        qpos = root['/observations/qpos'][()]
        qvel = root['/observations/qvel'][()]
        image_dict = dict()
        for cam_name in root[f'/observations/images/'].keys():
            image_dict[cam_name] = root[f'/observations/images/{cam_name}'][()]
        action = root['/action'][()]

    return qpos, qvel, action, image_dict

In [2]:
# play cam video
data_file = '/home/aidara/augmented_imitation_learning/training_data/randomstuff/threecolor_movement_1.hdf5'
#data_file = 'data/demo/trained.hdf5'
qpos, qvel, action, image_dict = load_hdf5(dataset_path=data_file)


In [3]:
for cam_name, image_list in image_dict.items():
    media.show_video(image_list, fps=30)

This browser does not support the video tag.


This browser does not support the video tag.


This browser does not support the video tag.


In [1]:
# plot qpos
plt.figure()
plt.plot(qpos, label=list(range(0, 9)))
plt.xlim((0,20))
plt.xlabel('step')
plt.ylabel('angle [rad]')
plt.title('joint positions')
plt.legend(loc='upper right')

plt.savefig('qpos.png')

NameError: name 'plt' is not defined

In [6]:
from franka_py import Robot, PDController, set_default_behavior, move_to_joint_position

robot = Robot("192.168.1.200")
set_default_behavior(robot)

state = robot.read_once()
print(state.q)
print(qpos[0][:7])
move_to_joint_position(robot, qpos[0][:7].tolist(), 0.5)



[0.04257679771134858, 0.055583129513151676, 0.049859077919659135, -1.7267239594428, 0.07649105225541944, 1.7980078186166377, 0.8056318778460222]
[-0.07582837  0.27359998 -0.35965207 -2.02358222  2.78561878  2.68760395
  1.06056869]


In [1]:
import numpy as np
import time

pd_controller = PDController(robot, np.array(state.q))
pd_controller.start()

for i,q in enumerate(qpos):
    q = q[:7]
    q = np.array(q)
    pd_controller.update_target(q)
    time.sleep(1)
    print(i, q)
    if i > 10:
        break
    
    
pd_controller.stop()

    
    

NameError: name 'PDController' is not defined

In [ ]:
for i,q in enumerate(qpos):
    before_q = robot.read_once()
    print(f"Before q: {before_q.q}")
    print(f"Target q: {q[:7]}")
    print(f"Difference: {np.linalg.norm(before_q.q - q[:7])}")
    print(f"The maximum difference is {np.max(np.abs(before_q.q - q[:7]))}")
    print(f"At the joint: {np.argmax(np.abs(before_q.q - q[:7]))}")
    q[5,]
    move_to_joint_position(robot, q[:7].tolist(), 0.1)
    curr_q = robot.read_once()
    if np.linalg.norm(curr_q.q - q[:7]) > 0.001:
        print(f"The robot has not reached the goal yet. This is the error: {np.linalg.norm(curr_q.q - q[:7])}")
        print("Stopping robot")
        move_to_joint_position(robot, q[:7].tolist(), 1)
        
    while np.linalg.norm(curr_q.dq) > 0.01:
        time.sleep(0.1)
        curr_q = robot.read_once()
        print(f"Current dq: {curr_q.dq}")
        print("Waiting for robot to stop")
        
        
    print(f"Step {i} done")
    if i > 10:
        break
robot.stop()
